![](https://github.com/bigdata-icict/ETL-Dataiku-DSS/raw/master/tutoriais/pcdas_1.5.png)

# Notebook para criação de tabela de indicadores da PNS -  módulo N 2019 Percepção do Estado de Saúde

## Bibliotecas Utilizadas

In [2]:
#Lendo pacotes necessários
library(survey)
library(ggplot2)
library(dplyr)
library(foreign)
library(forcats)
library(tidyverse)

## Carregando microdados da PNS

In [8]:
#Carregando banco de dados para R versão 3.5.0 ou superior
load("<coloque aqui o caminho para o arquivo dos microdados formato RDATA PNS 2019>")

#conferindo as dimensões (número de linhas e colunas)
dim("<Coloque aqui o nome do arquivo RDATA PNS 2019>")

[1] 293726   1087

## Definição do peso e filtragem de respondentes do questionário

In [9]:
#Selecionando registros válidos para o módulo P e calculando peso amostral - summary de verificação
pns2019.1<- <Coloque aqui o nome do arquivo RDATA>  %>% filter(V0025A==1)
pns2019.1<-pns2019.1 %>% mutate(peso_morador_selec=((V00291*(94114/168426190))))
pns2019.1<-pns2019.1 %>% filter(!is.na(peso_morador_selec))
summary(pns2019.1$peso_morador_selec)

    Min.  1st Qu.   Median     Mean  3rd Qu.     Max. 
 0.00582  0.27579  0.56358  1.03597  1.16822 63.29775 

## Criação de variáveis dos indicadores

In [10]:
#Desfechos - Indicadores

# Autoavaliação de saúde boa ou muito boa - N001P 
pns2019.1 <- pns2019.1 %>% mutate(N001P = if_else(N001 %in% 1:2,1,2,missing=2))
pns2019.1$N001P<-factor(pns2019.1$N001P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$N001P)

# Autoavaliação de saúde ruim ou muito ruim - N002P  
pns2019.1 <- pns2019.1 %>% mutate(N002P = if_else(N001 %in% 4:5,1,2,missing=2))
pns2019.1$N002P<-factor(pns2019.1$N002P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$N002P)

Sim   Não 
56822 34024

Sim   Não 
 6108 84738

## Definições de abrangências

### Situação urbana ou rural

In [11]:
#Situação Urbano ou Rural
pns2019.1 <- pns2019.1 %>% rename(Sit_Urbano_Rural=V0026)
pns2019.1$Sit_Urbano_Rural<-factor(pns2019.1$Sit_Urbano_Rural, levels=c(1,2), labels=c("urbano", "rural"))
summary(pns2019.1$Sit_Urbano_Rural)

urbano  rural 
 69873  20973

### Sexo

In [12]:
#Sexo
pns2019.1 <- pns2019.1 %>% rename(Sexo=C006)
pns2019.1$Sexo<-factor(pns2019.1$Sexo, levels=c(1,2), labels=c("Masculino", "Feminino"))
summary(pns2019.1$Sexo)

Masculino  Feminino 
    42799     48047

### UF

In [13]:
#Estados - UFs
pns2019.1 <- pns2019.1 %>% rename(Unidades_da_Federacao=V0001)
pns2019.1$Unidades_da_Federacao<-factor(pns2019.1$Unidades_da_Federacao, levels=c(11,12,13,14,15,16,17,21,22,23,24,25,26,27,28,29,31,32,33,35,41,42,43,50,51,52,53),
                                       label=c("Rondônia","Acre","Amazonas","Roraima","Pará","Amapá","Tocantins","Maranhão","Piauí","Ceará",
                                        "Rio Grande do Norte","Paraíba","Pernambuco","Alagoas","Sergipe","Bahia",
                                        "Minas Gerais","Espírito Santo","Rio de Janeiro","São Paulo",
                                        "Paraná","Santa Catarina","Rio Grande do Sul", 
                                        "Mato Grosso do Sul","Mato Grosso","Goiás","Distrito Federal"))
summary(pns2019.1$Unidades_da_Federacao)

Rondônia                Acre            Amazonas             Roraima 
               2176                2380                3479                2238 
               Pará               Amapá           Tocantins            Maranhão 
               3853                1554                1922                5080 
              Piauí               Ceará Rio Grande do Norte             Paraíba 
               2740                4265                2962                3158 
         Pernambuco             Alagoas             Sergipe               Bahia 
               4083                2987                2610                3659 
       Minas Gerais      Espírito Santo      Rio de Janeiro           São Paulo 
               5209                3541                4966                6114 
             Paraná      Santa Catarina   Rio Grande do Sul  Mato Grosso do Sul 
               3967                3738                3767                2863 
        Mato Grosso               Goiás    Distrito Federal 
               2468                2702                2365

### Grandes Regiões

In [14]:
#Grandes Regiões

pns2019.1 <- pns2019.1 %>% 
  mutate(GrandesRegioes = fct_collapse(Unidades_da_Federacao, 
                                          `Norte` = c("Rondônia","Acre","Amazonas","Roraima","Pará", "Amapá","Tocantins"),
                                          `Nordeste` = c("Maranhão", "Piauí", "Ceará", "Rio Grande do Norte", "Paraíba","Pernambuco", "Alagoas","Sergipe","Bahia"),
                                          `Sudeste` = c("Minas Gerais", "Espírito Santo","Rio de Janeiro", "São Paulo"), 
                                          `Sul` = c("Paraná", "Santa Catarina", "Rio Grande do Sul"),
                                          `Centro-Oeste`= c("Mato Grosso do Sul","Mato Grosso", "Goiás", "Distrito Federal")))
summary(pns2019.1$GrandesRegioes)

Norte     Nordeste      Sudeste          Sul Centro-Oeste 
       17602        31544        19830        11472        10398

### Capital

In [15]:
#Capital
pns2019.1<- pns2019.1 %>% mutate(Capital= fct_collapse(Unidades_da_Federacao,
                                        `Porto Velho`= "Rondônia", 
                                        `Boa Vista`= "Roraima",              
                                        `Rio Branco `= "Acre", 
                                        `Manaus` = "Amazonas",
                                        `Belém` = "Pará" ,
                                        `Macapá`= "Amapá",
                                        `Palmas` = "Tocantins",
                                        `São Luís` = "Maranhão",
                                        `Teresina`= "Piauí" ,
                                        `Fortaleza`= "Ceará",
                                        `Natal`= "Rio Grande do Norte",
                                        `João Pessoa`= "Paraíba",
                                        `Recife`= "Pernambuco",
                                        `Maceió`= "Alagoas",
                                        `Aracaju`= "Sergipe",
                                        `Salvador`= "Bahia",
                                        `Belo Horizonte`= "Minas Gerais",
                                        `Vitória`= "Espírito Santo",
                                        `Rio de Janeiro`= "Rio de Janeiro",
                                        `São Paulo`= "São Paulo",
                                        `Curitiba`= "Paraná",
                                        `Florianópolis`= "Santa Catarina",
                                        `Porto Alegre`= "Rio Grande do Sul",
                                        `Campo Grande`=  "Mato Grosso do Sul",
                                        `Cuiabá`= "Mato Grosso",
                                        `Goiânia` = "Goiás",
                                        `Brasília`= "Distrito Federal"))
summary(pns2019.1$Capital)

Porto Velho    Rio Branco          Manaus      Boa Vista          Belém 
          2176           2380           3479           2238           3853 
        Macapá         Palmas       São Luís       Teresina      Fortaleza 
          1554           1922           5080           2740           4265 
         Natal    João Pessoa         Recife         Maceió        Aracaju 
          2962           3158           4083           2987           2610 
      Salvador Belo Horizonte        Vitória Rio de Janeiro      São Paulo 
          3659           5209           3541           4966           6114 
      Curitiba  Florianópolis   Porto Alegre   Campo Grande         Cuiabá 
          3967           3738           3767           2863           2468 
       Goiânia       Brasília 
          2702           2365

### Faixa Etária

In [16]:
#Faixas Etárias
pns2019.1 <-  pns2019.1 %>% mutate(faixa_idade=cut(C008,
  breaks = c(18,30, 45, 60, 75,Inf),
  labels = c("18 a 29 anos","30 a 44 anos","45 a 59 anos","60 a 74 anos","75 anos ou mais"), 
  ordered_result = TRUE, right = FALSE))
summary(pns2019.1$faixa_idade) 

18 a 29 anos    30 a 44 anos    45 a 59 anos    60 a 74 anos 75 anos ou mais 
          15394           26754           23655           16767            5961 
           NA's 
           2315

### Raça

In [17]:
#Raça
pns2019.1 <- pns2019.1 %>% mutate(Raca= ifelse(C009==1, 1, 
                        ifelse(C009==2, 2, 
                            ifelse(C009==4, 3, 9))))

pns2019.1$Raca<-factor(pns2019.1$Raca, levels=c(1,2,3),labels=c("Branca", "Preta", "Parda"))

summary(pns2019.1$Raca)

Branca  Preta  Parda   NA's 
 33133  10345  45994   1374

### Renda per capita

In [18]:
#Rendimento domiciliar per capita
pns2019.1 <- pns2019.1 %>% mutate(rend_per_capita = ifelse(VDF004 %in% 1:2, 1, 
                        ifelse(VDF004%in% 3, 2, 
                        ifelse(VDF004%in% 4, 3,
                        ifelse(VDF004%in% 5, 4,5)))))

pns2019.1$rend_per_capita<-factor(pns2019.1$rend_per_capita, levels=c(1,2,3,4,5), labels=c("Até 1/2 SM","1/2 até 1 SM","1 até 2 SM",
                                                                                   "2 até 3 SM","Mais de 3 SM"))
summary(pns2019.1$rend_per_capita)


Até 1/2 SM 1/2 até 1 SM   1 até 2 SM   2 até 3 SM Mais de 3 SM 
       23697        26406        22466         7612        10665

### Escolariadade

In [19]:
# Escolaridade

pns2019.1 <- pns2019.1 %>% mutate(gescol = ifelse(VDD004A %in% 1:2, 1, 
                        ifelse(VDD004A%in% 3:4, 2, 
                        ifelse(VDD004A%in% 5:6, 3,4
                        ))))

pns2019.1$gescol<-factor(pns2019.1$gescol, levels=c(1,2,3,4), 
                                  labels=c("Sem instrução e fundamental incompleto","Fundamental completo e médio incompleto",
                                           "Médio completo e superior incompleto","Superior completo"))
summary(pns2019.1$gescol)

Sem instrução e fundamental incompleto Fundamental completo e médio incompleto 
                                  36276                                   13520 
   Médio completo e superior incompleto                       Superior completo 
                                  27433                                   13617

## Criando indicadores

### Filtrando base de indicadores

In [20]:
#Selecionando variáveis para cálculo de indicadores no survey
pns2019Nsurvey<- pns2019.1 %>% select("V0024","UPA_PNS","peso_morador_selec", "N001P","N002P",
                                     "C008","V0031","C009","Sit_Urbano_Rural","Sexo","Unidades_da_Federacao", "GrandesRegioes",
                                     "faixa_idade", "Raca","rend_per_capita","gescol","Capital")
summary(pns2019Nsurvey)

     V0024            UPA_PNS      peso_morador_selec N001P       N002P      
 1210010: 1167   140001681:   18   Min.   : 0.00582   Sim:56822   Sim: 6108  
 1410011:  792   140003815:   18   1st Qu.: 0.27579   Não:34024   Não:84738  
 2710111:  779   140005777:   18   Median : 0.56358                          
 2410011:  745   140006746:   18   Mean   : 1.03597                          
 5010011:  738   140007081:   18   3rd Qu.: 1.16822                          
 3210011:  711   140007715:   18   Max.   :63.29775                          
 (Other):85914   (Other)  :90738                                             
      C008            V0031            C009       Sit_Urbano_Rural
 Min.   : 15.00   Min.   :1.000   Min.   :1.000   urbano:69873    
 1st Qu.: 32.00   1st Qu.:1.000   1st Qu.:1.000   rural :20973    
 Median : 45.00   Median :2.000   Median :4.000                   
 Mean   : 46.39   Mean   :2.605   Mean   :2.679                   
 3rd Qu.: 60.00   3rd Qu.:4.000   3rd Qu.

### Exporta tabela filtrada com os dados específicos - Módulo N 2019

In [17]:
#Salvando csv para cálculo de indicadores no survey
diretorio_saida <- "<coloque aqui o diretório>"
write.csv(pns2019survey, file.path(diretorio_saida, "pns2019Nsurvey.csv"))

### Cria plano amostral complexo

In [21]:
#survey design
desPNSN=svydesign(id=~UPA_PNS, strat=~V0024, weight=~peso_morador_selec, nest=TRUE, data=pns2019Nsurvey)
desPNSN18=subset(desPNSN, C008>=18)
desPNSNC=svydesign(id=~UPA_PNS, strat=~V0024, weight=~peso_morador_selec, nest=TRUE, data=pns2019Nsurvey)
desPNSNC18=subset(desPNSNC, C008>=18 & V0031==1)
desPNSNR18=subset(desPNSN, C008>=18 & C009!=9)

### Criação da tabela de indicadores
Essa tabela é responsável por unir os indicadores no formato do painel de indicadores

In [22]:
matrizIndicadores = data.frame()

#### Definição de variáveis para iteração dos indicadores

In [23]:
ListaIndicadores = c(~N001P,~N002P)
ListaIndicadoresTexto = c("N001P","N002P")
ListaDominios = c(~Sexo,~Raca,~rend_per_capita,~faixa_idade,~Sit_Urbano_Rural,~Unidades_da_Federacao,~GrandesRegioes,~gescol,~Capital)
ListaDominiosTexto = c("sexo","raça","rend_per_capita","fx_idade_18","urb_rur","uf","região","gescol","capital")
ListaTotais = c('Brasil','Capital')
Ano <- "2019"

#### Preenchendo a tabela de indicadores
Essas iterações rodam por indicador, abrangência e por design

In [24]:
#Cálculo dos indicadores usando o pacote survey
i <- 0
for( indicador in ListaIndicadores){
    i <- i + 1
    j <- 1
    for (dominio in ListaDominios){
               if (ListaDominiosTexto[j]=="capital"){
                   dataframe_indicador<-svyby( indicador , dominio , desPNSNC18 , svymean,vartype= c("ci","cv"))
               }else if(ListaDominiosTexto[j]=="raça"){
                   dataframe_indicador<-svyby( indicador , dominio , desPNSNR18 , svymean,vartype= c("ci","cv"))
                  }else{ 
                    dataframe_indicador<-svyby( indicador , dominio , desPNSN18 , svymean,vartype= c("ci","cv"))
               }
               
              #União do dataframe de indicadores no formato do painel disponibilizado para PNS
               dataframe_indicador<-data.frame(dataframe_indicador)
               colnames(dataframe_indicador) <- c("abr_nome","Sim","Não","LowerS","LowerN","UpperS","UpperN","cvS","cvN")
               dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
               dataframe_indicador$abr_tipo <- ListaDominiosTexto[j]
               dataframe_indicador$Ano <- Ano
               dataframe_indicador <- dataframe_indicador %>% select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS","cvS")
               matrizIndicadores <-rbind(matrizIndicadores,dataframe_indicador)
               j <- j + 1
               
    }
}

#### Criando a tabela pela abrangência total

In [25]:
matriz_totais <- data.frame()

#### Preenchendo a tabela com as abrangencia Brasil e total das capitais

In [26]:
i=0
for(indicador in ListaIndicadores){
    i <- i+1
    for(total in ListaTotais){
        dataframe_indicador <- data.frame()
        dataframe_indicador_S <- data.frame()
        if(total == 'Capital'){
            dataframe_indicador <- svymean(indicador,desPNSNC18)
        }else{
            dataframe_indicador <- svymean(indicador,desPNSN18)
        }
        
       intervalo_confianca <- confint(dataframe_indicador)
        coeficiente_variacao <- cv(dataframe_indicador)
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(intervalo_confianca))
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(coeficiente_variacao))
        
        dataframe_indicador <- dataframe_indicador %>% 
                               select('mean','X2.5..','X97.5..',coeficiente_variacao) 
        dataframe_indicador_S <- dataframe_indicador %>% 
                                 slice(1)
                
        colnames(dataframe_indicador_S) <- c('Sim','LowerS','UpperS', 'cvS')
        dataframe_indicador_S$Indicador <- ListaIndicadoresTexto[i]
        dataframe_indicador_S$abr_tipo <- "total"
        dataframe_indicador_S$abr_nome <- total
        dataframe_indicador_S$Ano <- Ano 
        dataframe_indicador_S <- dataframe_indicador_S %>% 
                             select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS",'cvS')
        
        matriz_totais <-rbind(matriz_totais,dataframe_indicador_S)
        
    }
}


#### Unindo tabela de indicadores e de totais

In [27]:
matrizIndicadores<-rbind(matrizIndicadores,matriz_totais)

#### Visualizando a tabela de indicadores 

In [28]:
matrizIndicadores

abr_tipo        abr_nome            Ano  Indicador
Masculino           sexo            Masculino           2019 N001P    
Feminino            sexo            Feminino            2019 N001P    
Branca              raça            Branca              2019 N001P    
Preta               raça            Preta               2019 N001P    
Parda               raça            Parda               2019 N001P    
Até 1/2 SM          rend_per_capita Até 1/2 SM          2019 N001P    
1/2 até 1 SM        rend_per_capita 1/2 até 1 SM        2019 N001P    
1 até 2 SM          rend_per_capita 1 até 2 SM          2019 N001P    
2 até 3 SM          rend_per_capita 2 até 3 SM          2019 N001P    
Mais de 3 SM        rend_per_capita Mais de 3 SM        2019 N001P    
18 a 29 anos        fx_idade_18     18 a 29 anos        2019 N001P    
30 a 44 anos        fx_idade_18     30 a 44 anos        2019 N001P    
45 a 59 anos        fx_idade_18     45 a 59 anos        2019 N001P    
60 a 74 anos        fx_idade_18     60 a 74 anos        2019 N001P    
75 anos ou mais     fx_idade_18     75 anos ou mais     2019 N001P    
urbano              urb_rur         urbano              2019 N001P    
rural               urb_rur         rural               2019 N001P    
Rondônia            uf              Rondônia            2019 N001P    
Acre                uf              Acre                2019 N001P    
Amazonas            uf              Amazonas            2019 N001P    
Roraima             uf              Roraima             2019 N001P    
Pará                uf              Pará                2019 N001P    
Amapá               uf              Amapá               2019 N001P    
Tocantins           uf              Tocantins           2019 N001P    
Maranhão            uf              Maranhão            2019 N001P    
Piauí               uf              Piauí               2019 N001P    
Ceará               uf              Ceará               2019 N001P    
Rio Grande do Norte uf              Rio Grande do Norte 2019 N001P    
Paraíba             uf              Paraíba             2019 N001P    
Pernambuco          uf              Pernambuco          2019 N001P    
⋮                   ⋮               ⋮                   ⋮    ⋮        
Rio Branco 1        capital         Rio Branco          2019 N002P    
Manaus1             capital         Manaus              2019 N002P    
Boa Vista1          capital         Boa Vista           2019 N002P    
Belém1              capital         Belém               2019 N002P    
Macapá1             capital         Macapá              2019 N002P    
Palmas1             capital         Palmas              2019 N002P    
São Luís1           capital         São Luís            2019 N002P    
Teresina1           capital         Teresina            2019 N002P    
Fortaleza1          capital         Fortaleza           2019 N002P    
Natal1              capital         Natal               2019 N002P    
João Pessoa1        capital         João Pessoa         2019 N002P    
Recife1             capital         Recife              2019 N002P    
Maceió1             capital         Maceió              2019 N002P    
Aracaju1            capital         Aracaju             2019 N002P    
Salvador1           capital         Salvador            2019 N002P    
Belo Horizonte1     capital         Belo Horizonte      2019 N002P    
Vitória1            capital         Vitória             2019 N002P    
Rio de Janeiro3     capital         Rio de Janeiro      2019 N002P    
São Paulo2          capital         São Paulo           2019 N002P    
Curitiba1           capital         Curitiba            2019 N002P    
Florianópolis1      capital         Florianópolis       2019 N002P    
Porto Alegre1       capital         Porto Alegre        2019 N002P    
Campo Grande1       capital         Campo Grande        2019 N002P    
Cuiabá1             capital         Cuiabá              2019 N002P    
Goiânia1            capital         Goiânia 

#### Exportando tabela de indicadores calculados - Módulo N 2019

In [26]:
diretorio_saida <- "<coloque aqui o diretório>"
write.table(matrizIndicadores,file=paste0(diretorio_saida,"Indicadores_2019N_R.csv"),sep = ";",dec = ",",row.names = FALSE)